In [15]:
import numpy as np
import pandas as pd
from osgeo import gdal
from gdalconst import *
#import osr
import matplotlib.pyplot as plt
%matplotlib qt

#Import bokeh 
import bokeh.plotting as bp
from bokeh.models import ColumnDataSource, Label
from bokeh.layouts import layout

#package in this working directory
from utils.colormap import RGBAColorMapper
import netCDF4
from bokeh.palettes import RdBu11
#import color palettes for plotting raster
from bokeh.palettes import *


#Import dependencies and data for interactive map plot

import pandas as pd
import geopandas as gpd
from bokeh.models import HoverTool
from bokeh.palettes import RdYlBu11 as palette
from bokeh.models import LogColorMapper
import pysal as ps


#Importing raster data. 

from datashader.bokeh_ext import InteractiveImage, HoverLayer
import datashader as ds
import datashader.transfer_functions as tf
import rasterio as rio
from bokeh.plotting.figure import Figure
from skimage.transform import resize



bp.output_notebook()


Loading BokehJS ...

In [16]:
#Import the data

#Read a raster
Test_data = "/Users/bmelosh/VagrantBoxes/LSDTopoTools/Topographic_projects/Test_data/"
Test = gdal.Open(Test_data + "/Mandakini.bil")#Get raster data
M_DEM = Test.ReadAsArray()

#Read stream data
name = "Mandakini_fullProfileMC_forced_0.45_3_1258909000_10_80_281_for_Arc.csv" #Set file name
path = "/Users/bmelosh/VagrantBoxes/LSDTopoTools/Topographic_projects/Test_data/" #Set path to data
#for csv files
data = np.genfromtxt((path+name), delimiter=',', skip_header=1, names=['id', 'x', 'y', 'chan_number', 'reciever_chan','node_on_reciever_chan', 'node', 'row','column', 'flow_distance', 'chi', 'elevation', 'drainage_area', 'n_data_points', 'm_mean','m_st_dev', 'm_std_err', 'b_mean', 'b_st_dev', 'b_std_err', 'DW_mean', 'DW_st_dev', 'DW_std_err', 'fitted_elev_mean', 'fitted_elev_stdev', 'fitted_elev_std_err'])
#for tree files
#data = np.genfromtxt((path+name), delimiter=' ', skip_header=1, names=['chan_number', 'reciever_chan','node_on_reciever_chan', 'node', 'row','column', 'flow_distance', 'chi', 'elevation', 'drainage_area', 'n_data_points', 'm_mean','m_st_dev', 'm_std_err', 'b_mean', 'b_st_dev', 'b_std_err', 'DW_mean', 'DW_st_dev', 'DW_std_err', 'fitted_elev_mean', 'fitted_elev_stdev', 'fitted_elev_std_err'])

#load csv file as pandas dataframe
df = pd.read_csv(path+name)

##load Raster data
newpath = '/Users/bmelosh/VagrantBoxes/LSDTopoTools/Topographic_projects/Test_data/'
raster_data = rio.open(newpath+'Mandakini.bil')
xmin= 280000
ymin = 3350000
xmax = 345000
ymax = 3410000 #3632767

x_range = (xmin, xmax)
y_range = (ymin, ymax)

In [17]:
#playing with Pandas to plot data, trying to split individual channels.


# grid_fp = '/Users/bmelosh/projects/LSDTopoTools/MandakiniSHP/MandakiniSHP.shp'
# grid = gpd.read_file(grid_fp)

# import pandas as pd

# data = pd.read_csv((path))

# df = pd.DataFrame(data)

# unique_channels = df.channel_number.unique() #display different channels
# print(len(unique_channels))

# a = df.loc[df['channel_number'] == 0]
# b = df.loc[df['channel_number'] == 1]
# c = df.loc[df['channel_number'] == 2]
# d = df.loc[df['channel_number'] == 3]
# e = df.loc[df['channel_number'] == 4]

# grouped = df.groupby('channel_number')

# #for loop for dividing up the channel data
# # b = []
# # for i in range(0, len(unique_channels)): 
# #     a = df.loc[df['channel_number'] == i]
# #     a.
# grouped['elevation'].mean()


# # for i, group in grouped:
# #     #plt.figure()
# #     group.plot(x='x', y='y', title=str(i))


In [30]:
quickref  #For a quick reference of jupyter notebook shortcuts.

In [18]:
#Dealing with projections
# from pyproj import transform, Proj
# import numpy as np
# from bokeh.models.ranges import Range1d

# #input_proj = Proj(init='epsg:4326') #geographic
# #output_proj = Proj(init='epsg:3857') #web mercator
# input_proj = Proj(init='epsg:32644')
# output_proj = Proj(init='epsg:32644') 

# xmin_lng = 280000 #-139 #
# #, 3350000 (bottom left) 345000, 3410000 (top right)
# xmax_lng = 345000#-50

# ymin_lat = 3350000#20

# ymax_lat = 3410000 #55


# xmin_meters, ymin_meters = transform(input_proj, output_proj, xmin_lng, ymin_lat)
# xmax_meters, ymax_meters = transform(input_proj, output_proj, xmax_lng, ymax_lat)

# #reporjecting can be vectorized
# x_longitudes = np.array([280000, 345000])
# y_latitudes = np.array([3350000, 3410000])
# x_meters, y_meters = transform(input_proj, output_proj, x_longitudes, y_latitudes)

# #Bokeh 1D Ranges 
# x_range = Range1d(*x_meters)
# y_range = Range1d(*y_meters)

# print(x_meters)
# print(x_range)
# print(xmin_lng, xmin_meters)







In [9]:
x_range=(xmin, xmax)
y_range=(ymin, ymax)
source = ColumnDataSource(df)

p = bp.figure(x_range=x_range, y_range=y_range)
p.circle(df['x'][0],df['y'][0], source=source, color='red', size=20)
show(p)


In [22]:
import holoviews as hv
import geoviews as gv
from cartopy import crs


stream = gv.Dataset(df, kdims=['x', 'y', 'elevation', 'chi'])



streams = stream.to(gv.Points, kdims=['x', 'y'],
                    vdims=['elevation', 'chi'], crs=crs.PlateCarree())

%%output backend='bokeh'
%%opts Overlay [width=600 height=300 xaxis=None yaxis=None] 
%%opts Points (size=0.005 cmap='inferno') [tools=['hover'] color_index=2]

SyntaxError: invalid syntax (<ipython-input-22-2ab8eb786d70>, line 15)

In [32]:
from functools import partial
from datashader.utils import export_image
from datashader.colors import colormap_select, Greys9, Hot, viridis, inferno

import holoviews as hv
import geoviews as gv
from cartopy import crs

background = "black"

export = partial(export_image, background = background, export_path="export")
cm = partial(colormap_select, reverse=(background!="black"))

source = ColumnDataSource(df)

x_range=(xmin, xmax)
y_range=(ymin, ymax)


f = bp.figure(x_range=x_range, y_range=y_range)
f.circle(df['x'][0],df['y'][0], source=source, color='red', size=20)



def base_plot(tools='pan,wheel_zoom,reset',plot_width=900, plot_height=600, x_range=None, y_range=None, **plot_args):
    p = Figure(tools=tools, plot_width=plot_width, plot_height=plot_height,
              x_range=x_range, y_range=y_range, outline_line_color=None,
              min_border=0, min_border_left=0, min_border_right=0,
              min_border_top=0, min_border_bottom=0, **plot_args)
    
    p.axis.visible = False
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    #p.add_title(STAMEN_TONER, alpha=0.5)
    return p



def basic_raster(x_range, y_range, w, h, how='log'):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.raster(raster_data)
    return tf.shade(agg, cmap=cm(inferno), how='linear', alpha=255) #tf.interpolate(...cmap=['darkred', 'white', 'darkblue'])




# hover_layer = HoverLayer(agg=datashader_agg,
#                           extent=extent,
#                           field_name='elevation')

# f.renderers.append(hover_layer.renderer)
# f.add_tools(hover_layer.tool)
#glyph = ds.glyphs.Point(df['x'], df['y'])

ii = InteractiveImage(f, basic_raster)

# p = figure(title="Stream channel elevation map")
# p.circle(df['x'], df['y'], source=source, color='red', size=6)

ii



#show(f)


# put the subplots in a gridplot
#lay = layout([[left, right], [topo]])



# points = gv.Shape.from_shapefile(shape_path, crs=crs.PlateCarree())
# districts = gv.operation.project_shape(districts)

In [20]:
##HoverLayer example
from bokeh.io import output_notebook, show
from bokeh.plotting import Figure

import pandas as pd
import datashader as ds
import datashader.transfer_functions as tf

from datashader.colors import Hot

from datashader.bokeh_ext import HoverLayer



In [21]:
path = '/Users/bmelosh/VagrantBoxes/LSDTopoTools/Topographic_projects/Test_data/Mandakini_fullProfileMC_forced_0.45_3_1258909000_10_80_281_for_Arc.csv'

df = pd.read_csv(path, usecols=['x', 'y', 'flow_distance', 'elevation', 'chi'])
#df.head()
#df['hour'] = pd.to_datetime(df['tpep_dropoff_datetime']).dt.hour
df['elevation_cat'] = pd.cut(df['elevation'], bins=[0, 1000, 1500, 2700], labels=['low', 'mid', 'high']).astype('category')
#df.head(len(df))


In [22]:
df.head()

x            y  flow_distance         chi  elevation  \
0  328128.8534  3376368.352    48393.25000  169.116333     2617.0   
1  328040.0409  3376368.352    48304.43750  166.669403     2610.0   
2  327951.2284  3376368.352    48215.62500  164.225433     2584.0   
3  327862.4159  3376457.102    48090.02344  160.797958     2571.0   
4  327773.6034  3376457.102    48001.21094  158.416367     2562.0   

  elevation_cat  
0          high  
1          high  
2          high  
3          high  
4          high

In [23]:

def create_base_plot():
    
    # data is in meters
    xmin = 314000 
    ymin = 3368000
    xmax = 332000
    ymax = 3380000
    
    #Define plot canvas area
    cvs = ds.Canvas(plot_width=900,
                    plot_height=600,
                    x_range=(xmin, xmax),
                    y_range=(ymin, ymax))
    
    #
    agg = cvs.points(df, 'x', 'y', ds.mean('elevation'))
    img = tf.shade(agg, cmap=cm(inferno), how='log')
    fig = Figure(x_range=(xmin, xmax),
                 y_range=(ymin, ymax),
                 plot_width=900,
                 plot_height=600,
                 tools='')
    
    fig.background_fill_color = 'black'
    fig.toolbar_location = None
    fig.axis.visible = False
    fig.grid.grid_line_alpha = 0
    fig.min_border_left = 0
    fig.min_border_right = 0
    fig.min_border_top = 0
    fig.min_border_bottom = 0

    fig.image_rgba(image=[img.data],
                   x=[xmin],
                   y=[ymin],
                   dw=[xmax-xmin],
                   dh=[ymax-ymin])
    return fig, (xmin, ymin, xmax, ymax), agg

fig, extent, datashader_agg = create_base_plot()

#

In [24]:
# #define area in utm coord.
# xmin = 314000
# ymin = 3368000
# xmax = 332000
# ymax = 3380000

# fig, extent, datashader_agg = create_base_plot()

# hover_layer = HoverLayer(agg=datashader_agg,
#                          extent=extent,
#                          field_name='elevation')

# fig.renderers.append(hover_layer.renderer)
# fig.add_tools(hover_layer.tool)
# show(fig)

In [42]:
#may 8th , monday, plotting coordinates and datashader rasters
cvs = ds.Canvas(plot_width=900,
                    plot_height=600,
                    x_range=(xmin, xmax),
                    y_range=(ymin, ymax))


#%time tf.shade(cvs.points(df,'x','y'))
glyph = ds.glyphs.Point('x', 'y')

from datashader import reductions
reduction = reductions.count()

from datashader.core import bypixel
agg = bypixel(df, cvs, glyph, reduction)



In [30]:
#Best way to display stream as a datashader image, although this is probably not the way to go.


#tf.shade(cvs.points(df, 'x', 'y', agg=reductions.mean('elevation')))

# cvs = ds.Canvas(plot_width=900, plot_height=900, x_range=(314000,332000),y_range=(3368000,3380000))
# aggr = reductions.mean('elevation')
# img = cvs.points(df, 'x', 'y',agg=aggr)
# tfimg = tf.shade(img, cmap=[(230,230,0), "orangered", "#300030"])
# tf.spread(tfimg)




In [25]:
import bokeh.plotting as bp
from datashader.bokeh_ext import InteractiveImage

bp.output_notebook()

#Bokeh figure, set data source
source=ColumnDataSource(df)


#p = bp.figure(tools='pan,wheel_zoom,reset', x_range=x_range, y_range=y_range)

#p.circle(pdata['x'], pdata['y'], source=source, color='red', size=6)

#setting interactive plot
#my_hover = HoverTool()
#my_hover.tooltips = [('Elevation (m)', '@elevation'), ('Chi (X)', '@chi')]
#p.add_tools(my_hover)



#function to create datashader image
def image_callback(x_range, y_range, w, h):
    cvs = ds.Canvas(plot_width=w, plot_height=h, x_range=x_range, y_range=y_range)
    agg = cvs.points(df, 'x', 'y', ds.reductions.mean('elevation'))
    img = tf.shade(agg)
    return tf.spread(img)#, threshold=0.80)





p = bp.figure(x_range=x_range, y_range=y_range)
p.circle(df['x'][0],df['y'][0], source=source, color='red', size=20)


#interactive image for the raster
#InteractiveImage(p, basic_raster)



#image_callback((314000,332000),(3368000,3380000), 2000, 2000)

#interactive image for the stream
InteractiveImage(p, image_callback)

Loading BokehJS ...

In [29]:
from bokeh.plotting import figure, output_file, show
from bokeh.models import HoverTool

#Set data and data source, ongoing work would be to do this from within the pandas dataframe
x = df['x']
y = df['y']
chi = df['chi']
elevation = df['elevation']
flow_distance = df['flow_distance']
source = ColumnDataSource({'x': x, 'y': y, 'chi': chi, 'elevation': elevation, 'flow_distance': flow_distance})


#define tools to use
TOOLS = "pan,wheel_zoom,reset,save,lasso_select"


# Basic plot setup
plot = figure(plot_width=600, plot_height=300, title='Stream Map')
plot.circle(x, y, size=2, color='gray')
cr = plot.circle(x='x', y='y', size=20,
                fill_color="grey", hover_fill_color="firebrick",
                fill_alpha=0.03, hover_alpha=0.3,
                line_color=None, hover_line_color="white", source=source)
plot.add_tools(HoverTool(tooltips=None, renderers=[cr], mode='mouse'))


plot2 = figure(plot_width=500, plot_height=250, y_range=y_range, toolbar_location='above', 
               title='Elevation profile', x_axis_label='Flow Distance (m)', y_axis_label='Elevation (m)')
plot2.circle(flow_distance, elevation, size=2, color='gray')
cr2 = plot2.circle(x='flow_distance', y='elevation', size=20,
                 fill_color='grey', hover_fill_color="firebrick",
                 fill_alpha=0.03, hover_alpha=0.3,
                 line_color=None, hover_line_color="white", source=source)
plot2.add_tools(HoverTool(tooltips=None, renderers=[cr2], mode='mouse'))

plot3 = figure(plot_width=500, plot_height=250, y_range=plot2.y_range, toolbar_location='above', 
               title='Chi profile', x_axis_label='Chi (X)', y_axis_label='Elevation (m)')
plot3.circle(chi, elevation, size=2, color=colors)
cr3 = plot3.circle(x='chi', y='elevation', size=20,
                 fill_color='grey', hover_fill_color="firebrick",
                 fill_alpha=0.03, hover_alpha=0.3,
                 line_color=None, hover_line_color="white", source=source)
plot3.add_tools(HoverTool(tooltips=None, renderers=[cr3], mode='mouse'))




out = layout([[plot],[plot2], [plot3]])



show(out)


In [26]:
#using matplot lib colors in bokeh
import matplotlib as mpl

colors = ["#%02x%02x%02x" % (int(r), int(g), int(b)) for r, g, b, _ in 255*mpl.cm.jet(mpl.colors.Normalize()(chi))]


In [108]:
#makes jupyter notebook screen wider
from IPython.core.display import HTML, display
display(HTML("<style>.container { width:80% !important; }</style>"))

Loading BokehJS ...